#### Problem Statment:
    - Classify 2 different art periods using convolutional neural networks. The art periods I have choosen are impressionism and romanticism.

#### Overview:
    - Looking at the metadata of the images, I will pick two periods that are similar yet different. I choose impressionism, and romanticism for the following reasons:
        - The classes are fairly balanced.
        - Both the Romanticism and Impressionist styles were around the same time and the same place.
        - Both periods have similar but different influences.
        
#### Proposed Methods & Model:
    - I will use convolutional neural network in a seperate jupyter notebook. The image preprocessing and data agumentation is done by ImageDataGenerator.
    
#### Data:
    - The link to the dataset from kaggle:
    https://www.kaggle.com/c/painter-by-numbers/data
    
    - I uploaded the metadata to see what are the periods and artist, which is how I was able to identify which periods I will be looking at. Next I will start to separate the images and metadata for my project into their own folders.
    

In [1]:
#capstone eda from csv file

In [1]:
import pandas as pd
import os

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
#pd.set_option('display.width', 1000)

In [2]:
# read in the meta data
df_all = pd.read_csv('./all_data_info.csv')

In [3]:
# Looking at all the artist and the amount of works for each artist.
df_all['artist'].value_counts()

Zdislav Beksinski                                                                              500
Ilya Repin                                                                                     500
Giovanni Battista Piranesi                                                                     500
Ivan Aivazovsky                                                                                500
Albrecht Durer                                                                                 500
Rembrandt                                                                                      500
Pierre-Auguste Renoir                                                                          500
Gustave Dore                                                                                   500
Ivan Shishkin                                                                                  500
John Singer Sargent                                                                            500
Pablo Pica

In [4]:
# Looking at all the styles and the amount of styles for each category
# Here I chose my top 3 which are Impressionism, Realism, Romanticism.
# They have similaries and differences, and not a large class imbalance.
df_all['style'].value_counts()

Impressionism                   10643
Realism                         10523
Romanticism                      9285
Expressionism                    7013
Post-Impressionism               5778
Art Nouveau (Modern)             4899
Baroque                          4400
Surrealism                       4167
Symbolism                        3476
Rococo                           2733
Northern Renaissance             2379
Naïve Art (Primitivism)          2295
Abstract Expressionism           2074
Neoclassicism                    2038
Cubism                           1747
Ukiyo-e                          1426
Early Renaissance                1351
Mannerism (Late Renaissance)     1342
High Renaissance                 1314
Art Informel                     1267
Magic Realism                    1002
Abstract Art                      979
Academicism                       972
Color Field Painting              910
Pop Art                           791
Fauvism                           731
Lyrical Abst

In [5]:
df_all.head()

artist    date     genre  pixelsx  pixelsy  size_bytes   source  \
0  Barnett Newman  1955.0  abstract  15530.0   6911.0   9201912.0  wikiart   
1  Barnett Newman  1950.0  abstract  14559.0   6866.0   8867532.0  wikiart   
2     kiri nichol  2013.0       NaN   9003.0   9004.0   1756681.0      NaN   
3     kiri nichol  2013.0       NaN   9003.0   9004.0   1942046.0      NaN   
4     kiri nichol  2013.0       NaN   9003.0   9004.0   1526212.0      NaN   

                  style                  title artist_group  in_train  \
0  Color Field Painting                  Uriel   train_only      True   
1  Color Field Painting  Vir Heroicus Sublimis   train_only      True   
2         Neoplasticism                    NaN    test_only     False   
3         Neoplasticism                    NaN    test_only     False   
4         Neoplasticism                    NaN    test_only     False   

  new_filename  
0   102257.jpg  
1    75232.jpg  
2    32145.jpg  
3    20304.jpg  
4      836.jpg

In [6]:
# creating a new dataframe with style and new_filename next to each other
df_all_1 = df_all[['style', 'new_filename', 'title', 'source', 'size_bytes',
                  'pixelsy', 'pixelsx', 'genre', 'date', 'artist']]

In [7]:
df_all_1.head(10)

style new_filename  \
0  Color Field Painting   102257.jpg   
1  Color Field Painting    75232.jpg   
2         Neoplasticism    32145.jpg   
3         Neoplasticism    20304.jpg   
4         Neoplasticism      836.jpg   
5              Yamato-e    29855.jpg   
6  Color Field Painting    62252.jpg   
7               Ukiyo-e    49823.jpg   
8  Color Field Painting    63861.jpg   
9           Romanticism    84512.jpg   

                                         title   source  size_bytes  pixelsy  \
0                                        Uriel  wikiart   9201912.0   6911.0   
1                        Vir Heroicus Sublimis  wikiart   8867532.0   6866.0   
2                                          NaN      NaN   1756681.0   9004.0   
3                                          NaN      NaN   1942046.0   9004.0   
4                                          NaN      NaN   1526212.0   9004.0   
5  Night March of a Hundred Demons (left half)  wikiart  10496349.0   3000.0   
6     Who’s Afraid of Red,  Yellow and Blue II  wikiart   6383948.0   8640.0   
7        Small Bird on a Branch of Kaidozakura  wikiart  12762418.0   9276.0   
8                                Black Fire I   wikiart   1135960.0   8206.0   
9                        Procession in Naples   wikiart   7896792.0   7352.0   

   pixelsx                     genre    date                     artist  
0  15530.0                  abstract  1955.0             Barnett Newman  
1  14559.0                  abstract  1950.0             Barnett Newman  
2   9003.0                       NaN  2013.0                kiri nichol  
3   9003.0                       NaN  2013.0                kiri nichol  
4   9003.0                       NaN  2013.0                kiri nichol  
5  25528.0     mythological painting     NaN              Tosa Mitsuoki  
6   7345.0                  abstract     NaN             Barnett Newman  
7   6483.0  bird-and-flower painting    1838                  Hiroshige  
8   6049.0                  abstract  1963.0             Barnett Newman  
9   6238.0                 cityscape     NaN  Franz Richard Unterberger

In [8]:
#df_all_1.drop
# creating new variable excludes the styles I am interested in and then dorpping it.
indexNames = df_all_1[(df_all_1['style'] != 'Romanticism') & (df_all_1['style'] != 'Impressionism')].index

# Delete these row indexes from dataFrame
df_all_1.drop(indexNames , inplace=True)

C:\Users\Vera\Anaconda3\lib\site-packages\pandas\core\frame.py:4117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [9]:
df_all_1.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 19928 entries, 9 to 103232
Data columns (total 10 columns):
style           19928 non-null object
new_filename    19928 non-null object
title           19928 non-null object
source          19928 non-null object
size_bytes      19928 non-null float64
pixelsy         19928 non-null float64
pixelsx         19928 non-null float64
genre           19882 non-null object
date            14819 non-null object
artist          19928 non-null object
dtypes: float64(3), object(7)
memory usage: 1.7+ MB


In [10]:
df_all_1.head(2)

style new_filename                  title   source  size_bytes  \
9   Romanticism    84512.jpg  Procession in Naples   wikiart   7896792.0   
14  Romanticism    99442.jpg           Storm at sea  wikiart   3189597.0   

    pixelsy  pixelsx      genre  date                     artist  
9    7352.0   6238.0  cityscape   NaN  Franz Richard Unterberger  
14   5811.0   7444.0     marina  1873            Ivan Aivazovsky

In [11]:
# Checking to make sure the styles I want are created
df_all_1['style'].value_counts()

Impressionism    10643
Romanticism       9285
Name: style, dtype: int64

In [12]:
# saving the dataframe 
#df_all_1.to_csv('./updated_all_data.csv', index=False) 

- the code above was already ran prior.

In [22]:
df_all_1['artist'].value_counts()

Gustave Dore                                             500
Ivan Aivazovsky                                          500
Claude Monet                                             494
Childe Hassam                                            492
Pierre-Auguste Renoir                                    486
Edgar Degas                                              481
Alfred Sisley                                            452
Camille Pissarro                                         445
Eugene Boudin                                            441
Francisco Goya                                           386
William Merritt Chase                                    304
Charles M. Russell                                       275
Konstantin Makovsky                                      274
Konstantin Korovin                                       265
Mary Cassatt                                             263
John Singer Sargent                                      243
Berthe Morisot          

created masks to search for different images that are well known in each style, or by artist that are well known. To do some eda on the images.

In [47]:
mask2 = ((df_all_1['style'] == 'Impressionism') & (df_all_1['artist'] == 'Claude Monet') & (df_all_1['title'].str.contains("Camille")))

In [48]:
df_all_1[mask2]

style new_filename  \
1580   Impressionism    61167.jpg   
2529   Impressionism    35377.jpg   
9751   Impressionism    54749.jpg   
9769   Impressionism    37640.jpg   
11182  Impressionism    88147.jpg   
12576  Impressionism    31858.jpg   
15673  Impressionism    24910.jpg   

                                                   title   source  size_bytes  \
1580   Camille Monet and a Child in the Artist’s Gard...  wikiart   4166741.0   
2529   Camille Monet in the Garden at the House in Ar...  wikiart   2569609.0   
9751                         Camille Monet in the Garden  wikiart   1042301.0   
9769   Camille and Jean Monet in the Garden at Argent...  wikiart    368358.0   
11182                  Camille on the Beach at Trouville  wikiart    839352.0   
12576            Camille Monet at the Window, Argentuile  wikiart    855626.0   
15673                         Camille with Green Parasol  wikiart    656337.0   

       pixelsy  pixelsx           genre  date        artist  
1580    2586.0   3060.0        portrait  1875  Claude Monet  
2529    3000.0   2184.0       landscape  1876  Claude Monet  
9751    1485.0   2000.0        portrait  1873  Claude Monet  
9769    1997.0   1486.0  genre painting  1873  Claude Monet  
11182   1478.0   1800.0        portrait  1870  Claude Monet  
12576   1701.0   1392.0        portrait  1873  Claude Monet  
15673   1600.0   1159.0        portrait  1876  Claude Monet

In [66]:
mask3 = ((df_all_1['style'] == 'Romanticism') & (df_all_1['artist'].str.contains("Delacroix")) & (df_all_1['title'].str.contains("Death")))

In [67]:
df_all_1[mask3]

style new_filename                                 title  \
13182  Romanticism    90455.jpg                 Death of Sardanapalus   
30142  Romanticism    56858.jpg                  The Death of Ophelia   
40876  Romanticism    43181.jpg  Sketch for The Death of Sardanapalus   
43147  Romanticism    39439.jpg                  The Death of Ophelia   

        source  size_bytes  pixelsy  pixelsx                  genre  date  \
13182  wikiart   2698378.0   1333.0   1679.0  mythological painting  1827   
30142  wikiart    189174.0    900.0   1096.0      literary painting  1838   
40876  wikiart    108225.0    770.0   1038.0       sketch and study  1827   
43147  wikiart    181216.0    754.0   1031.0      literary painting  1843   

                 artist  
13182  Eugene Delacroix  
30142  Eugene Delacroix  
40876  Eugene Delacroix  
43147  Eugene Delacroix

In [43]:
mask1 = ((df_all_1['style'] == 'Impresionism') & (df_all_1['artist'] == 'Edgar Degas') & (df_all_1['new_filename']))

In [44]:
df_all_1[mask1]

style new_filename  \
147    Impressionism    95360.jpg   
791    Impressionism    92192.jpg   
1268   Impressionism    99133.jpg   
1273   Impressionism    52238.jpg   
1424   Impressionism    98645.jpg   
1476   Impressionism    62534.jpg   
1578   Impressionism    14705.jpg   
1620   Impressionism    96144.jpg   
1700   Impressionism     2570.jpg   
1752   Impressionism    44311.jpg   
1774   Impressionism    93521.jpg   
1780   Impressionism    78280.jpg   
1816   Impressionism    11295.jpg   
1829   Impressionism     7614.jpg   
1837   Impressionism    84017.jpg   
1840   Impressionism    44022.jpg   
1886   Impressionism    42660.jpg   
1895   Impressionism    28594.jpg   
1920   Impressionism    63091.jpg   
1938   Impressionism    36886.jpg   
1954   Impressionism    23523.jpg   
1967   Impressionism    33351.jpg   
1975   Impressionism    95494.jpg   
1987   Impressionism    58952.jpg   
1996   Impressionism    26979.jpg   
2005   Impressionism    20745.jpg   
2014   Impressionism     5701.jpg   
2022   Impressionism    17412.jpg   
2030   Impressionism    76222.jpg   
2096   Impressionism     9295.jpg   
2105   Impressionism    97509.jpg   
2144   Impressionism    95079.jpg   
2227   Impressionism    43448.jpg   
2275   Impressionism     3266.jpg   
2290   Impressionism    51486.jpg   
2324   Impressionism    71777.jpg   
2345   Impressionism    80726.jpg   
2357   Impressionism     1171.jpg   
2438   Impressionism    66726.jpg   
2525   Impressionism    64247.jpg   
2537   Impressionism    37227.jpg   
2567   Impressionism   102012.jpg   
2572   Impressionism    57321.jpg   
2639   Impressionism    80074.jpg   
2681   Impressionism    72875.jpg   
2793   Impressionism    43916.jpg   
2865   Impressionism    51594.jpg   
2867   Impressionism    16846.jpg   
3063   Impressionism    39095.jpg   
3134   Impressionism    27765.jpg   
3181   Impressionism    86120.jpg   
3234   Impressionism    18446.jpg   
3574   Impressionism    57800.jpg   
3590   Impressionism    72591.jpg   
3629   Impressionism    61438.jpg   
3655   Impressionism    34647.jpg   
3698   Impressionism    77001.jpg   
3853   Impressionism    26182.jpg   
3869   Impressionism    66688.jpg   
4155   Impressionism     7938.jpg   
4372   Impressionism    19644.jpg   
4406   Impressionism    96730.jpg   
4443   Impressionism    58105.jpg   
4567   Impressionism    21813.jpg   
4568   Impressionism    43862.jpg   
4603   Impressionism    75781.jpg   
4705   Impressionism    15904.jpg   
4897   Impressionism    52197.jpg   
5040   Impressionism    88559.jpg   
5173   Impressionism    96593.jpg   
5217   Impressionism     4462.jpg   
5678   Impressionism    10970.jpg   
6112   Impressionism    40783.jpg   
6119   Impressionism    96381.jpg   
6227   Impressionism    23470.jpg   
6477   Impressionism    33584.jpg   
6739   Impressionism    64069.jpg   
7081   Impressionism     2936.jpg   
7257   Impressionism    12508.jpg   
7432   Impressionism    44288.jpg   
7471   Impressionism     3103.jpg   
7661   Impressionism    17176.jpg   
7731   Impressionism    58204.jpg   
7764   Impressionism    84675.jpg   
7849   Impressionism    21235.jpg   
7887   Impressionism    10308.jpg   
7898   Impressionism    19904.jpg   
7939   Impressionism    18779.jpg   
8291   Impressionism    29248.jpg   
8342   Impressionism    25988.jpg   
8367   Impressionism    92005.jpg   
8464   Impressionism    21764.jpg   
8469   Impressionism    37881.jpg   
8660   Impressionism    23793.jpg   
8667   Impressionism     8526.jpg   
8817   Impressionism   103135.jpg   
8854   Impressionism    85346.jpg   
8987   Impressionism    58749.jpg   
9059   Impressionism    85820.jpg   
9275   Impressionism     8995.jpg   
9335   Impressionism    62062.jpg   
9336   Impressionism    48117.jpg   
9356   Impressionism    54286.jpg   
9469   Impressionism    65890.jpg   
9496   Impressionism    63867.jpg   
9559   Impressionism    93301.jpg   
9657   Impressionism    87363.jpg   
9665   Impressionis

In [18]:
df_all_1[['artist', 'title', 'new_filename', 'style']]

artist  \
9                               Franz Richard Unterberger   
14                                        Ivan Aivazovsky   
25                                            Jan Matejko   
28                                           Gustave Dore   
29                                           Gustave Dore   
34                                           Gustave Dore   
66                                         William Turner   
82                                        Ivan Aivazovsky   
96                                    Gustave Caillebotte   
115                                      Ferdinand Hodler   
132                                 Theo van Rysselberghe   
136                                        Rudolf von Alt   
137                                        Rudolf von Alt   
147                                           Edgar Degas   
174                             Franz Richard Unterberger   
184                                 Akseli Gallen-Kallela   
193                                        Alfred Stevens   
199                                           Karl Bodmer   
216                                          Claude Monet   
218                                      Ferdinand Hodler   
223                                           Karl Bodmer   
232                                           Karl Bodmer   
239                                           Paul Signac   
242                                           Karl Bodmer   
264                                           Karl Bodmer   
276                                        Rudolf von Alt   
277                                      Ferdinand Hodler   
279                                 Pierre-Auguste Renoir   
289                                           Karl Bodmer   
292                                           Paul Signac   
301                                      Ferdinand Hodler   
316                                           Karl Bodmer   
318                                        Rudolf von Alt   
320                                           Karl Bodmer   
322                                      Ferdinand Hodler   
327                                        Francisco Goya   
334                                          David Wilkie   
337                                           Karl Bodmer   
338                                        Valentin Serov   
343                                  Pierre-Paul Prud'hon   
346                                           Karl Bodmer   
357                                           Thomas Cole   
359                                      Ferdinand Hodler   
369                                        Rudolf von Alt   
377                                       Orest Kiprensky   
386                                    Eugene von Guerard   
400                                         Alfred Sisley   
402                                           Paul Signac   
404                                        Rudolf von Alt   
410                                        Rudolf von Alt   
413                                           Karl Bodmer   
415                                        Rudolf von Alt   
416                                        Rudolf von Alt   
418                                      Ferdinand Hodler   
422                                           Karl Bodmer   
425                                        Rudolf von Alt   
433                                           Karl Bodmer   
439                                Dante Gabriel Rossetti   
442                                        Rudolf von Alt   
447                                        Rudolf von Alt   
448                                           Leon Bonnat   
453                                        Rudolf von Alt   
454                                    Theodore Gericault   
462                              Sir Lawrence Alma-Tadema   
466                                        Rudolf von Alt   
479                      

use updated df to create some sort of list, and try to iterate through the list, if file in folder is in this list then use the, comand that move into a new folder that i would then work with

In [12]:
name_and_style = df_all_1[['new_filename', 'style']]

In [13]:
name_and_style.head()

new_filename        style
9     84512.jpg  Romanticism
14    99442.jpg  Romanticism
25    75956.jpg  Romanticism
28     7486.jpg  Romanticism
29    35766.jpg  Romanticism

In [14]:
name_and_style.to_csv('./binary_names_style.csv', index=False) 